## SDK code to create ITEM_Quantity_Z_Score_to_CUSTOMER_item_Quantity_14d

Feature description:
>Z-Score of the item Quantity in relation to the distribution of item Quantity among all items with the same customer as that item over a 14d period.

In [ ]:
import featurebyte as fb
fb.use_profile("tutorial")

### Activate catalog

 See [SDK reference for catalogs](https://docs.featurebyte.com/latest/reference/core/catalog/)

In [ ]:
catalog = fb.Catalog.activate("Grocery Dataset Tutorial")

### Set windows for aggregation

In [ ]:
windows = ['14d']

### Get view from table
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")

### Create Lookup feature
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to declare a lookup feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.ViewColumn.as_feature/)

In [ ]:
# Create lookup feature from Quantity column for item entity.
item_quantity =\
invoiceitems_view["Quantity"].as_feature("ITEM_Quantity")

### Do window aggregation from INVOICEITEMS
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to groupby a view](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)

 See [SDK reference to do aggregation over time](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate_over/)

 See [SDK reference for feature group](https://docs.featurebyte.com/latest/reference/core/feature_group/)

 See [list of aggregation operations](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)

In [ ]:
# Group INVOICEITEMS view by customer entity (GroceryCustomerGuid).
invoiceitems_view_by_customer =\
invoiceitems_view.groupby(['GroceryCustomerGuid'])

In [ ]:
# Get Avg of Quantity for the customer over time.
feature_group =\
invoiceitems_view_by_customer.aggregate_over(
    "Quantity", method="avg",
    feature_names=[
        "CUSTOMER_Avg_of_item_Quantity"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get CUSTOMER_Avg_of_item_Quantity_14d object from feature group.
customer_avg_of_item_quantity_14d =\
feature_group["CUSTOMER_Avg_of_item_Quantity_14d"]

In [ ]:
# Get Std of Quantity for the customer over time.
feature_group =\
invoiceitems_view_by_customer.aggregate_over(
    "Quantity", method="std",
    feature_names=[
        "CUSTOMER_Std_of_item_Quantity"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get CUSTOMER_Std_of_item_Quantity_14d object from feature group.
customer_std_of_item_quantity_14d =\
feature_group["CUSTOMER_Std_of_item_Quantity_14d"]

### Compare lookup with aggregation
 See [list of feature transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)

In [ ]:
# Get the Z-Score of the item Quantity in relation to the distribution of item Quantity among all
# items with the same customer as that item over a 14d period.
item_quantity_z_score_to_customer_item_quantity_14d = (
    item_quantity
    - customer_avg_of_item_quantity_14d
) / customer_std_of_item_quantity_14d
# Give a name to new feature
item_quantity_z_score_to_customer_item_quantity_14d.name = \
"ITEM_Quantity_Z_Score_to_CUSTOMER_item_Quantity_14d"

### Preview feature
 Read on [the feature primary entity concept](https://docs.featurebyte.com/latest/about/glossary/#feature-primary-entity)

 Read on [the serving entity concept](https://docs.featurebyte.com/latest/about/glossary/#serving-entity)

 See [SDK reference for observation table](https://docs.featurebyte.com/latest/reference/core/observation_table/)

 See [SDK reference to preview feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)

In [ ]:
#Check the primary entity of the feature'
item_quantity_z_score_to_customer_item_quantity_14d.primary_entity

In [ ]:
#Get observation table: 'Preview Table with 10 items'
preview_table = catalog.get_observation_table(
	"Preview Table with 10 items"
)

In [ ]:
#Preview ITEM_Quantity_Z_Score_to_CUSTOMER_item_Quantity_14d
item_quantity_z_score_to_customer_item_quantity_14d.preview(
	preview_table
)

### Save feature
 See [SDK reference to save feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)

In [ ]:
# Save feature
item_quantity_z_score_to_customer_item_quantity_14d.save()

### Add description and see feature definition file
 See [SDK reference for the definition file of a feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.definition/)

In [ ]:
# Add description
item_quantity_z_score_to_customer_item_quantity_14d.update_description(
	"Z-Score of the item Quantity in relation to the distribution of item "
	"Quantity among all items with the same customer as that item over a "
	"14d period."
)
# See feature definition file
item_quantity_z_score_to_customer_item_quantity_14d.definition